
## Uk Crime 

For this project, I have selected the UK Police API as the data source. The API provides detailed crime data across various categories for the specified locations and dates. The specific endpoint used is:

https://data.police.uk/api/crimes-street/all-crime?lat=52.629729&lng=-1.131592&date=2023-01

The producer and consumer were implemented using kafka and java, the producer fetches data fro the api and sends it to the consumer. The consumer writes the data to csv files that are used for this analysis and visualization. 

Because of the nature of the api that when you call a get request it gets you the data for specific area that is bounded by the longitude and latituted, eg. lat and lng that are in the api URL. Because that area is too narrow i wanted to analyse the whole area of london.

I created a box area the size of London based on the cities latitude and longitude:

        double minLat = 51.286;
        double maxLat = 51.686;
        double minLng = -0.510;
        double maxLng = 0.334;

        double latStep = 0.05;
        double lngStep = 0.05;

The steps are used for iteration in this virtual box they can be vertically and horizontally. The coordinates are placed in the api in the producer and the producer scans the city of London that we bounded.

Because i wanted to analyse crime overtime i had to increment the number of the month in the api URL. That way i got that through every iteration i scanned the city of London for every month of the year. 

The official data UK government API provides.

| Column Name      | Description                                                                                 |
|------------------|---------------------------------------------------------------------------------------------|
| `category`       | The category of the crime, providing a clear description of the type of offense committed.   |
| `persistent_id`  | A 64-character unique identifier for each crime. This ID is persistent and remains the same. |
| `month`          | The month when the crime occurred.                                                          |
| `location`       | The approximate location of the crime.                                                      |
| `latitude`       | The latitude of the crime's location.                                                       |
| `longitude`      | The longitude of the crime's location.                                                      |
| `street`         | The approximate street where the crime occurred.                                            |
| `id`             | A unique identifier for the street where the crime occurred.                                |
| `name`           | Name of the location. Note that this is only an approximation of where the crime happened.   |
| `location_type`  | Type of the location (Force or BTP). Force indicates a normal police location; BTP refers to British Transport Police. |
| `location_subtype`| For BTP locations, this specifies the type of location (e.g., train station).               |
| `outcome_status` | The outcome of the crime, including the category and date of the latest recorded outcome.    |


In the kafka consumer i divided the data into to files that are used for location based analysis, streaming analysis and general purpose analysis. The streaming files are divided in batches of files that are around 10k rows. Those files are then use to mimic near real time data streaming.

The crime location csv contains columns: 
| Column Name   | Description                                                               |
|---------------|---------------------------------------------------------------------------|
| `Latitude`    | The geographical latitude of the location where the crime occurred.        |
| `Longitude`   | The geographical longitude of the location where the crime occurred.       |
| `Category`    | The category of the crime (e.g., violent crime, theft, etc.).              |



The general purpose analysis csv contains columns: 

| Column Name        | Description                                                                            |
|--------------------|----------------------------------------------------------------------------------------|
| `ID`               | Unique identifier for the crime. This ID is related to the API and is not a police identifier. |
| `Category`         | The type or category of crime (e.g., violent crime, theft, etc.).                       |
| `Location Type`    | Indicates the type of location (Force or BTP). "Force" means a normal police area, while "BTP" refers to British Transport Police areas. |
| `Street ID`        | A unique identifier for the street where the crime occurred.                            |
| `Street Name`      | The name of the street where the crime was approximately recorded.                      |
| `Outcome Status`   | The status and result of the crime investigation (e.g., charged, under investigation, no further action). |
| `Month`            | The month when the crime was recorded.                                                  |

The streaming csv files contain columns:

| Column Name        | Description                                                                            |
|--------------------|----------------------------------------------------------------------------------------|
| `Category`         | The type or category of crime (e.g., violent crime, theft, etc.).                       |
| `Month`            | The month when the crime was recorded.                                                  |





##Analysing Location dataset 

####General purpose crime analysis

#####Crime locations by category

This code reads a CSV file containing location data into a DataFrame and processes it for further analysis. It converts the Latitude and Longitude columns to DoubleType for accurate numerical operations. A new column with random values is added to shuffle the DataFrame rows, which helps in randomizing the order of records. Finally, the DataFrame is reordered based on these random values, and the temporary random column is dropped.

Shuffling the data is essential for ensuring that any subsequent analyses or modeling is unbiased and not influenced by the original order of the records. This process can help in achieving more reliable and generalized results, especially in tasks like training machine learning.

In [0]:
from pyspark.sql.functions import col,rand
from pyspark.sql.types import DoubleType
#file_location = "/FileStore/tables/final_location_dataset.csv"

file_location = "/FileStore/tables/final_location_dataset.csv"
file_type = "csv"

df_loc = spark.read.option("header", "true").csv(file_location)
df_loc.cache()

df_loc = df_loc.withColumn("Latitude", col("Latitude").cast(DoubleType())) \
                   .withColumn("Longitude", col("Longitude").cast(DoubleType()))

df_loc = df_loc.withColumn("random", rand())

df_loc_shuffled = df_loc.orderBy("random").drop("random")


display(df_loc_shuffled)

Latitude Longitude Category 51.530566 -0.200361 burglary 51.428319 -0.056586 violent-crime 51.49321 -0.145896 public-order 51.589936 -0.145063 other-theft 51.446419 0.224786 public-order 51.53119 -0.119727 theft-from-the-person 51.47472 -0.122756 violent-crime 51.596023 0.032546 vehicle-crime 51.534751 0.118739 public-order 51.374541 -0.451792 violent-crime 51.546296 -0.103975 violent-crime 51.482654 -0.214994 other-theft 51.442202 -0.042413 other-theft 51.53668 -0.206147 anti-social-behaviour 51.539394 -0.054266 anti-social-behaviour 51.543769 0.004228 anti-social-behaviour 51.548223 -0.059068 burglary 51.447424 0.181817 violent-crime 51.527805 -0.352707 violent-crime 51.577985 -0.011572 other-theft 51.628715 -0.070545 anti-social-behaviour 51.585046 0.031854 vehicle-crime 51.546133 -0.252792 other-theft 51.336951 -0.117062 shoplifting 51.479302 -0.158182 vehicle-crime 51.48351 -0.319824 anti-social-behaviour 51.57962 -0.278872 violent-crime 51.585575 -0.032431 bicycle-theft 51.385093 -0.420394 anti-social-behaviour 51.433125 0.255951 violent-crime 51.376364 -0.049864 public-order 51.590235 -0.017591 other-theft 51.52227 -0.157481 violent-crime 51.544266 0.002505 robbery 51.58046 -0.02073 other-theft 51.480088 -0.015142 violent-crime 51.48156 -0.010728 theft-from-the-person 51.540728 -0.141556 anti-social-behaviour 51.531417 0.059527 anti-social-behaviour 51.534705 0.024608 other-theft 51.439403 -0.126492 burglary 51.53969 -0.142983 public-order 51.42743 -0.158557 violent-crime 51.386171 -0.111607 vehicle-crime 51.526732 -0.0273 shoplifting 51.541979 -0.001013 theft-from-the-person 51.538681 0.051967 public-order 51.48258 0.075199 violent-crime 51.493632 -0.261009 anti-social-behaviour 51.48156 -0.010728 burglary 51.531593 0.049485 anti-social-behaviour 51.5373 -0.361016 other-crime 51.530183 -0.12307 anti-social-behaviour 51.581073 0.021371 bicycle-theft 51.530183 -0.12307 other-theft 51.540595 -0.144307 other-theft 51.487227 -0.218329 violent-crime 51.52693 -0.100311 theft-from-the-person 51.472562 -0.0104 violent-crime 51.576807 -0.2938 theft-from-the-person 51.545212 0.148258 vehicle-crime 51.541098 -0.071427 other-theft 51.423902 -0.002992 public-order 51.485012 -0.24496 violent-crime 51.549568 -0.055015 anti-social-behaviour 51.688163 -0.032514 public-order 51.596507 -0.253328 drugs 51.384054 -0.189429 violent-crime 51.431331 -0.388619 violent-crime 51.382 0.085003 vehicle-crime 51.629443 -0.100799 burglary 51.635665 -0.343065 anti-social-behaviour 51.281373 0.187748 public-order 51.631436 -0.431185 burglary 51.388362 -0.181943 violent-crime 51.587639 0.08199 other-theft 51.643093 -0.163548 vehicle-crime 51.475996 -0.12603 possession-of-weapons 51.495143 -0.015208 burglary 51.53119 -0.119727 anti-social-behaviour 51.538052 -0.188905 anti-social-behaviour 51.628782 -0.40842 anti-social-behaviour 51.487414 0.145885 other-theft 51.391818 -0.159053 other-theft 51.382079 -0.128977 criminal-damage-arson 51.538948 0.051099 violent-crime 51.59267 -0.325674 anti-social-behaviour 51.493964 -0.206614 violent-crime 51.489246 -0.038857 violent-crime 51.582391 -0.373553 vehicle-crime 51.584356 -0.06564 burglary 51.493347 -0.093957 anti-social-behaviour 51.535082 -0.169081 criminal-damage-arson 51.540543 -0.190652 anti-social-behaviour 51.540652 -0.24582 anti-social-behaviour 51.581431 0.054094 anti-social-behaviour 51.546252 0.084139 drugs 51.439934 0.270851 shoplifting 51.533273 -0.029122 shoplifting 51.542698 -0.180038 public-order 51.590247 -0.081039 anti-social-behaviour 51.584488 -0.440626 other-theft 51.532718 -0.447254 burglary 51.484319 0.139042 violent-crime 51.372378 -0.207935 violent-crime 51.499385 -0.16753 other-theft 51.491897 -0.128446 anti-social-behaviour 51.532947 -0.204895 drugs 51.592095 0.001619 drugs 51.423902 -0.002992 shoplifting 51.587633 -0.158683 anti-social-behaviour 51.533766 -0.324102 drugs 51.486987 -0.179852 vehicle-crime 51.53024 -0.155593 other-theft 51.598655 -0.069509 violent-crime 51.540309 -0.009

Databricks visualization. Run in Databricks to view.

####Analysing and reverse geocoding the location data
This code performs reverse geocoding to convert latitude and longitude coordinates into city names using the reverse_geocode library. It then adds a city column to the DataFrame based on these coordinates. The analysis focuses on violent crimes, filtering the data to only include records with the violent-crime category. It aggregates violent crime counts by city and identifies the top 10 areas with the highest number of violent crimes. Additionally, it identifies the top 10 most dangerous and safest areas overall based on all crime types.

Converts spatial coordinates into meaningful city names, making it easier to analyze crime data by geographic locations.
Helps to identify the areas with the highest incidence of violent crimes, which can inform public safety efforts and resource allocation.
Provides insights into both the most dangerous and safest areas based on the total number of reported crimes, aiding in crime prevention strategies and urban planning.

In [0]:
%pip install reverse_geocode

Python interpreter will be restarted.
Python interpreter will be restarted.


In [0]:
import reverse_geocode
from pyspark.sql.types import *
from pyspark.sql.functions import *


file_location = "/FileStore/tables/final_location_dataset.csv"
file_type = "csv"

df_loc = spark.read.option("header", "true").csv(file_location)
df_loc.cache()

#westminster 51.494720, -0.135278
x = 51.494720
y = -0.135278
coordinates = [(x,y)]
data = reverse_geocode.search(coordinates) 
print(data)


#UDF reverse geocoding
def get_city(lat, lon):
    coordinates = [(lat, lon)]
    result = reverse_geocode.search(coordinates)
    return result[0]['city'] if result else None

get_city_udf = udf(lambda lat, lon: get_city(lat, lon), StringType())

df_with_city = df_loc.withColumn('city', get_city_udf(col('latitude'), col('longitude')))
df_with_city.cache()


violent_crimes_df = df_with_city.filter(col('category') == 'violent-crime')

violent_crimes_df.cache()

violent_crimes_by_area = violent_crimes_df.groupBy('city').agg(count("*").alias("violent_crime_count"))

most_violent_area = violent_crimes_by_area.orderBy(col("violent_crime_count").desc()).limit(10)

# top 10 most violent areas
display(most_violent_area)

crimes_by_area = df_with_city.groupBy('city').agg(count("*").alias("crime_count"))
most_dangerous_area = crimes_by_area.orderBy(col("crime_count").desc())

#top 10 most dangerous areas with all types of crimes
display(most_dangerous_area.limit(10))


#top 10 safest areas in london
safest_areas = crimes_by_area.orderBy(col("crime_count").asc())
display(safest_areas.limit(10))


#city centre areas 



[{'country_code': 'GB', 'city': 'City of Westminster', 'latitude': 51.4975, 'longitude': -0.1357, 'population': 247614, 'state': 'England', 'county': 'Greater London', 'country': 'United Kingdom'}]


city violent_crime_count Croydon 2337 Barking 1623 West Ham 1609 Harlesden 1583 Bow 1509 Bethnal Green 1407 East Ham 1396 Kennington 1354 Walthamstow 1346 Peckham 1265

Databricks visualization. Run in Databricks to view.

city crime_count Croydon 9000 Bethnal Green 6947 King's Cross 6912 East Ham 6645 Barking 6454 Kennington 5951 West Ham 5857 Walthamstow 5836 Bow 5675 Harlesden 5625

Databricks visualization. Run in Databricks to view.

city crime_count Nutfield 1 West Horndon 1 Hadley Wood 2 West Clandon 2 Kings Langley 3 New Denham 4 High Ongar 5 Grays 8 Gerrards Cross 8 Bricket Wood 9

Databricks visualization. Run in Databricks to view.

#####Central London Crime Analysis

This code filters crime data to focus on central London areas, aggregates the crime counts for each area, and compares the total crime in central London with the total crime across all of London. It identifies specific areas such as Soho, Covent Garden, and Mayfair, and computes the crime count for each location. The code also creates a comparison DataFrame showing the proportion of crimes in central London relative to the entire city.

This analysis is useful for identifying how much crime occurs in specific central London areas, which is valuable for policy-making, safety measures, and resource distribution.
By comparing crime in central London to the entire city, it helps understand whether central areas are more or less crime-prone compared to the broader London region. This data can help with targeted policing and crime prevention strategies.

In [0]:
from pyspark.sql.types import LongType, StructType, StructField
from pyspark.sql.functions import sum as _sum

# List of central London areas for comparison
central_london_areas = [
    'Soho',
    'Covent Garden',
    'Holborn',
    'Mayfair',
    'Marylebone',
    'Fitzrovia',
    'Bloomsbury',
    'St. James\'s',
    'Victoria',
    'King\'s Cross',
    'Paddington',
    'Southbank',
    'Pimlico',
    'Clerkenwell',
    'Knightsbridge',
    'Belgravia',
    'West End',
    'Bayswater',
    'Chelsea',
    'Kensington',
    'Charing Cross',
    'Aldwych',
    'Temple',
    'Lambeth',
    'Vauxhall',
    'Borough',
    'London Bridge',
    'Shoreditch',
    'Whitechapel',
    'Spitalfields',
    'Barbican',
    'Farringdon',
    'South Kensington',
    'Hyde Park',
    'Regent\'s Park',
    'Somers Town',
    'Elephant and Castle',
    'Bermondsey',
    'Notting Hill',
    'Euston'
]
#
central_london_crimes = df_with_city.filter(col('city').isin(central_london_areas))
central_london_crimes.cache()

central_crime_stats = central_london_crimes.groupBy('city').agg(count("*").alias("crime_count"))

total_crime_in_central = central_crime_stats.agg(_sum('crime_count').alias('total_central_crime')).collect()[0][0]

total_crime_in_london = crimes_by_area.agg(_sum('crime_count').alias('total_london_crime')).collect()[0][0]

comparison_data = [(total_crime_in_central, total_crime_in_london)]

schema = StructType([
    StructField("Total Central London Crime", LongType(), True),
    StructField("Total London Crime", LongType(), True)
])

comparison_df = spark.createDataFrame(comparison_data, schema)

display(central_crime_stats)

display(comparison_df)


city crime_count Pimlico 3932 Marylebone 861 Regent's Park 830 Clerkenwell 2030 Barbican 1102 Holborn 72 Kensington 27 Chelsea 5252 Lambeth 2545 Whitechapel 655 West End 21 King's Cross 6912 Spitalfields 2076

Databricks visualization. Run in Databricks to view.

Total Central London Crime Total London Crime 26315 383245

####General Purpose Dataset Analysis

#####Cleaning and editing the data

The dataset was loaded and cleaned by converting relevant columns to appropriate data types and handling missing values with default entries. Column names were standardized for consistency, and entries with generic street names were replaced with "Unknown". The resulting DataFrame is now prepared for analysis and visualization.

In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *


file_location = "/FileStore/tables/ukYearFull.csv"
file_type = "csv"
df = spark.read.option("header", "true").csv(file_location)

# Data cleanup
df_cleaned = df.withColumn("ID", col("ID").cast(IntegerType())) \
               .withColumn("Latitude", col("Latitude").cast(DoubleType())) \
               .withColumn("Longitude", col("Longitude").cast(DoubleType())) \
               .withColumn("Month", col("Month").cast(DateType())) 

df_cleaned = df_cleaned.fillna({
  'Street Name':'Unknown',
  'Outcome Status':'Unknown'
})            
df_cleaned = df_cleaned.withColumnRenamed('Location Type', 'location_type') \
       .withColumnRenamed('Street ID', 'street_id') \
       .withColumnRenamed('Street Name', 'street_name') \
       .withColumnRenamed('Outcome Status', 'outcome_status') \
       .withColumnRenamed('Month', 'month') \
       .withColumnRenamed('Category', 'category') \
       .withColumnRenamed('Latitude', 'latitude') \
       .withColumnRenamed('Longitude', 'longitude') 



df_cleaned = df_cleaned.withColumn("street_name", when(trim(col("street_name")) == "On or near", "Unknown").otherwise(col("street_name")))

display(df_cleaned)

ID category location_type latitude longitude street_id street_name outcome_status month 107810326 anti-social-behaviour Force 51.291537 -0.528145 2003082 On or near Tannery Lane Unknown 2023-01-01 107810050 anti-social-behaviour Force 51.27786 -0.526116 2003033 On or near Woodhill Unknown 2023-01-01 107806339 burglary Force 51.27786 -0.526116 2003033 On or near Woodhill Court result unavailable 2023-01-01 107805369 burglary Force 51.291537 -0.528145 2003082 On or near Tannery Lane Investigation complete; no suspect identified 2023-01-01 107805381 criminal-damage-arson Force 51.297943 -0.499382 2003938 On or near Haynes Close Investigation complete; no suspect identified 2023-01-01 107805526 other-theft Force 51.287223 -0.503574 2003725 On or near Kiln Lane Investigation complete; no suspect identified 2023-01-01 107811525 other-theft Force 51.293127 -0.489886 2004029 Unknown Investigation complete; no suspect identified 2023-01-01 107808100 other-theft Force 51.284942 -0.53293 2002809 On or near Send Hill Status update unavailable 2023-01-01 107806909 other-theft Force 51.297943 -0.499382 2003938 On or near Haynes Close Investigation complete; no suspect identified 2023-01-01 107810282 other-theft Force 51.293127 -0.489886 2004029 Unknown Investigation complete; no suspect identified 2023-01-01 107809708 other-theft Force 51.293127 -0.489886 2004029 Unknown Investigation complete; no suspect identified 2023-01-01 107809935 public-order Force 51.288872 -0.530037 2003009 On or near Sandfields Investigation complete; no suspect identified 2023-01-01 107805017 public-order Force 51.293127 -0.489886 2004029 Unknown Unable to prosecute suspect 2023-01-01 107809108 violent-crime Force 51.297943 -0.499382 2003938 On or near Haynes Close Unable to prosecute suspect 2023-01-01 107806089 violent-crime Force 51.286306 -0.507777 2003656 On or near Maple Road Further investigation is not in the public interest 2023-01-01 107809889 violent-crime Force 51.288872 -0.530037 2003009 On or near Sandfields Investigation complete; no suspect identified 2023-01-01 107805329 violent-crime Force 51.297943 -0.499382 2003938 On or near Haynes Close Unable to prosecute suspect 2023-01-01 107804960 violent-crime Force 51.293127 -0.489886 2004029 Unknown Unable to prosecute suspect 2023-01-01 107810667 anti-social-behaviour Force 51.291076 -0.3902 2006668 Unknown Unknown 2023-01-01 107809704 burglary Force 51.290121 -0.423569 2006107 On or near Fairways Investigation complete; no suspect identified 2023-01-01 107804988 burglary Force 51.2915 -0.421758 2006221 On or near Lovelace Close Investigation complete; no suspect identified 2023-01-01 107807846 other-theft Force 51.279809 -0.405139 2006651 On or near Effingham Common Road Investigation complete; no suspect identified 2023-01-01 107807383 vehicle-crime Force 51.284473 -0.427505 2005977 On or near Falconwood Investigation complete; no suspect identified 2023-01-01 107805984 violent-crime Force 51.283253 -0.388056 2007046 On or near Fox Lane Unable to prosecute suspect 2023-01-01 107811221 violent-crime Force 51.285996 -0.424427 2006217 On or near Orchard Close Unable to prosecute suspect 2023-01-01 107810334 anti-social-behaviour Force 51.289348 -0.31757 2008869 On or near Yarm Close Unknown 2023-01-01 107804708 anti-social-behaviour Force 51.296268 -0.321706 2008749 On or near St John's Road Unknown 2023-01-01 107807186 anti-social-behaviour Force 51.294053 -0.322719 2008739 On or near Poplar Avenue Unknown 2023-01-01 107805933 anti-social-behaviour Force 51.276761 -0.321557 2008697 On or near Mickleham Drive Unknown 2023-01-01 107809172 criminal-damage-arson Force 51.294998 -0.322799 2008737 On or near Poplar Road Investigation complete; no suspect identified 2023-01-01 107810075 criminal-damage-arson Force 51.285425 -0.295701 2009100 Unknown Investigation complete; no suspect identified 2023-01-01 107808571 other-theft Force 51.279678 -0.321163 2008760 On or near The Downs Status update unavailable 

#####Most Common Outcomes for Each Category
Retrieves the most frequent outcome for each crime category based on the counts.
Highlights the most common resolution for each crime type, which can be useful for assessing patterns in crime resolution.

In [0]:
# Most Common Outcome for Each Category
spark.sql("""
SELECT category, outcome_status, count as most_likely_outcome
FROM (
    SELECT category, outcome_status, count,
           ROW_NUMBER() OVER (PARTITION BY category ORDER BY count DESC) as row_num
    FROM category_outcome
) tmp
WHERE row_num = 1
""").display()


category outcome_status most_likely_outcome anti-social-behaviour Unknown 21702 bicycle-theft Investigation complete; no suspect identified 1551 burglary Investigation complete; no suspect identified 4408 criminal-damage-arson Investigation complete; no suspect identified 5376 drugs Investigation complete; no suspect identified 1344 other-crime Investigation complete; no suspect identified 631 other-theft Investigation complete; no suspect identified 9877 possession-of-weapons Court result unavailable 221 public-order Investigation complete; no suspect identified 4783 robbery Investigation complete; no suspect identified 2245 shoplifting Investigation complete; no suspect identified 5283 theft-from-the-person Investigation complete; no suspect identified 3732 vehicle-crime Investigation complete; no suspect identified 9752 violent-crime Investigation complete; no suspect identified 19176

Databricks visualization. Run in Databricks to view.

#####Most Crimes per Relative Location of Crime
Counts crimes by street name and ranks them by frequency.
Helps identify streets with the highest number of crimes, which can be useful for targeting interventions and resource allocation.

In [0]:
# Most Crimes per Relative Location of Crime
most_crimes_per_relative_location = df_cleaned.filter(col("street_name") != "Unknown") \
    .groupBy("street_name") \
    .agg(count("*").alias("crime_count")) \
    .orderBy(col("crime_count").desc())
display(most_crimes_per_relative_location.limit(10))


street_name crime_count On or near Supermarket 3237 On or near Shopping Area 2999 On or near Parking Area 2519 On or near Petrol Station 1323 On or near Nightclub 700 On or near Further/higher Educational Building 681 On or near Hospital 649 On or near North End 553 On or near Theatre/concert Hall 542 On or near Sports/recreation Area 526

Databricks visualization. Run in Databricks to view.

#####Crimes by Street ID

Aggregates and counts crimes by street ID, ordering by frequency.
Provides insights into crime distribution based on street IDs, allowing for identification of high-crime areas for focused investigation and management.

In [0]:
# Most Crimes per Street ID
most_crimes_per_street_id = df_cleaned.groupBy("street_id") \
    .agg(count("*").alias("crime_count")) \
    .orderBy(col("crime_count").desc())

# Top 10 Street IDs with Crimes
display(most_crimes_per_street_id.limit(10))


street_id crime_count 2136892 445 1665456 364 1708460 332 1683607 318 1681353 304 1657768 288 1681290 284 1665604 278 1679222 272 1693220 268

Databricks visualization. Run in Databricks to view.

####Streaming Dataset Analysis

In the consumer the data was batch written to csv files that are used for near real time streaming in databricks.
The files contain about 10k lines each. They were stored in the stream_data_dir directory in databricks. 

In [0]:
%fs ls /FileStore/tables/stream_data_dir

path name size modificationTime dbfs:/FileStore/tables/stream_data_dir/stream_1.csv stream_1.csv 239705 1725564101000 dbfs:/FileStore/tables/stream_data_dir/stream_10-1.csv stream_10-1.csv 242137 1725564122000 dbfs:/FileStore/tables/stream_data_dir/stream_10.csv stream_10.csv 243261 1725553728000 dbfs:/FileStore/tables/stream_data_dir/stream_11-1.csv stream_11-1.csv 242317 1725564126000 dbfs:/FileStore/tables/stream_data_dir/stream_11.csv stream_11.csv 243363 1725553734000 dbfs:/FileStore/tables/stream_data_dir/stream_12-1.csv stream_12-1.csv 241254 1725564129000 dbfs:/FileStore/tables/stream_data_dir/stream_12.csv stream_12.csv 243551 1725553741000 dbfs:/FileStore/tables/stream_data_dir/stream_13-1.csv stream_13-1.csv 242230 1725564131000 dbfs:/FileStore/tables/stream_data_dir/stream_13.csv stream_13.csv 245984 1725553748000 dbfs:/FileStore/tables/stream_data_dir/stream_14-1.csv stream_14-1.csv 246285 1725564133000 dbfs:/FileStore/tables/stream_data_dir/stream_14.csv stream_14.csv 245672 1725553754000 dbfs:/FileStore/tables/stream_data_dir/stream_15-1.csv stream_15-1.csv 243372 1725564136000 dbfs:/FileStore/tables/stream_data_dir/stream_15.csv stream_15.csv 245820 1725553761000 dbfs:/FileStore/tables/stream_data_dir/stream_16-1.csv stream_16-1.csv 242927 1725564138000 dbfs:/FileStore/tables/stream_data_dir/stream_16.csv stream_16.csv 246755 1725553768000 dbfs:/FileStore/tables/stream_data_dir/stream_17-1.csv stream_17-1.csv 243585 1725564141000 dbfs:/FileStore/tables/stream_data_dir/stream_17.csv stream_17.csv 245424 1725553775000 dbfs:/FileStore/tables/stream_data_dir/stream_18-1.csv stream_18-1.csv 244885 1725564148000 dbfs:/FileStore/tables/stream_data_dir/stream_18.csv stream_18.csv 247957 1725553775000 dbfs:/FileStore/tables/stream_data_dir/stream_19-1.csv stream_19-1.csv 247186 1725564155000 dbfs:/FileStore/tables/stream_data_dir/stream_19.csv stream_19.csv 244345 1725553780000 dbfs:/FileStore/tables/stream_data_dir/stream_2-1.csv stream_2-1.csv 240266 1725564101000 dbfs:/FileStore/tables/stream_data_dir/stream_2.csv stream_2.csv 241384 1725553676000 dbfs:/FileStore/tables/stream_data_dir/stream_20-1.csv stream_20-1.csv 243124 1725564158000 dbfs:/FileStore/tables/stream_data_dir/stream_20.csv stream_20.csv 247612 1725553781000 dbfs:/FileStore/tables/stream_data_dir/stream_21-1.csv stream_21-1.csv 243477 1725564160000 dbfs:/FileStore/tables/stream_data_dir/stream_21.csv stream_21.csv 245541 1725553784000 dbfs:/FileStore/tables/stream_data_dir/stream_22-1.csv stream_22-1.csv 243575 1725564163000 dbfs:/FileStore/tables/stream_data_dir/stream_22.csv stream_22.csv 246224 1725553786000 dbfs:/FileStore/tables/stream_data_dir/stream_23-1.csv stream_23-1.csv 245536 1725564166000 dbfs:/FileStore/tables/stream_data_dir/stream_23.csv stream_23.csv 248222 1725553789000 dbfs:/FileStore/tables/stream_data_dir/stream_24-1.csv stream_24-1.csv 243443 1725564170000 dbfs:/FileStore/tables/stream_data_dir/stream_24.csv stream_24.csv 245037 1725553790000 dbfs:/FileStore/tables/stream_data_dir/stream_25-1.csv stream_25-1.csv 245248 1725564175000 dbfs:/FileStore/tables/stream_data_dir/stream_25.csv stream_25.csv 247456 1725553794000 dbfs:/FileStore/tables/stream_data_dir/stream_26-1.csv stream_26-1.csv 244919 1725564178000 dbfs:/FileStore/tables/stream_data_dir/stream_26.csv stream_26.csv 246671 1725553795000 dbfs:/FileStore/tables/stream_data_dir/stream_27-1.csv stream_27-1.csv 245199 1725564181000 dbfs:/FileStore/tables/stream_data_dir/stream_27.csv stream_27.csv 247005 1725553799000 dbfs:/FileStore/tables/stream_data_dir/stream_28-1.csv stream_28-1.csv 248279 1725564183000 dbfs:/FileStore/tables/stream_data_dir/stream_28.csv stream_28.csv 247238 1725553800000 dbfs:/FileStore/tables/stream_data_dir/stream_29-1.csv stream_29-1.csv 243147 1725564186000 dbfs:/FileStore/tables/stream_data_dir/stream_29.csv stream_29.csv 246396 1725553804000 dbfs:/FileStore/tables/stream_data_dir/stream_3-1.csv stream_3-1.csv 241053 1725564104000 dbfs:/FileStore/

#####Crimes per Category Streaming
This code is designed to process and stream crime data in real-time. It reads CSV files containing crime categories, processes the data incrementally as new files arrive, and calculates the count of crimes per category. The processed data is stored in memory for real-time visualization or further analysis.
This setup is valuable for streaming and tracking crime patterns as data is updated. It can be used to monitor crime categories as they increase or decrease over time in near real-time.

In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *

file_location = "/FileStore/tables/stream_data_dir"

schema = StructType([
    StructField("Category", StringType(), True)
])

df_stream = spark.readStream.schema(schema).option("maxFilesPerTrigger", 1).csv(file_location)
# df_stream.cache()


# display(df_stream)


df_counts = df_stream.groupBy("Category").agg(count("Category").alias("Count"))
df_counts.isStreaming
 # df_counts.cache()

spark.conf.set("spark.sql.shuffle.partitions", "2")  

query = (
  df_counts
    .writeStream
    .format("memory")       
    .queryName("scounts")     
    .outputMode("complete")  
    .trigger(availableNow=True)
    .start()
)

query.awaitTermination(10)


Out[7]: False

In [0]:
display(spark.sql("SELECT * FROM scounts ORDER BY Count DESC"))



Category Count violent-crime 184568 anti-social-behaviour 147988 other-theft 77751 vehicle-crime 71015 public-order 42461 criminal-damage-arson 41202 shoplifting 40441 burglary 35862 theft-from-the-person 31946 drugs 25807 robbery 18852 bicycle-theft 11351 other-crime 7419 Category 3976 possession-of-weapons 3887

Databricks visualization. Run in Databricks to view.

####Violent Crimes over Time

This code streams and analyzes crime data, specifically focusing on violent crimes. It reads incoming crime data files, filters them for violent crimes, and groups them by month to count occurrences. The results are stored in memory for real-time querying and visualization.

This analysis is useful for real-time monitoring of violent crimes, allowing users to observe how such crimes evolve over time, month by month.

In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *

# File location and schema
file_location = "/FileStore/tables/stream_data_dir"

schema = StructType([
    StructField("Category", StringType(), True),
    StructField("Month", StringType(), True)
])

df_stream = spark.readStream.schema(schema).option("maxFilesPerTrigger", 1).csv(file_location)

violent_crimes_df = df_stream.filter(col("Category") == "violent-crime")

df_counts = violent_crimes_df.groupBy("Month").agg(count("Category").alias("Count"))

query = (
  df_counts
    .writeStream
    .format("memory")
    .queryName("violent_crimes_counts")
    .outputMode("complete")  
    .trigger(processingTime='10 seconds')  
    .start()
)

query.awaitTermination(10) 


Out[39]: False

In [0]:
display(spark.table("violent_crimes_counts"))


Month Count 2023-07 10969 2023-06 12173 2023-09 8847 2023-03 10403 2023-02 8841 2023-05 11076 2023-01 6700 2023-08 7931 2023-04 9795

Databricks visualization. Run in Databricks to view.